Import Libraries

In [1]:
import sqlite3
import requests
from tqdm import tqdm

from flask import Flask, request
import json 
import numpy as np
import pandas as pd

# Introduction
In most cases when we are running a business, there are a lot of data stakeholder outside our company. The problem is that we need to provide the access in a way that they will not break our security rules or concerns. One way to solve that is by creating an API for the database. In this project, we will introduce you on how python is used for data transaction management using Flask API. 

**Usecase**: Bikeshare App\
Have you ever rent a bike for faster mobility in town? In the past few years, this business once become a phenomenom. In Indonesia, there are lots of similar services, for example, the Jakarta government's "GOWES" bike sharing service that launcehd in July 2020. 

For the user perspective, the general journey is denoted as follows:
- User scan the bike located at some bike station, sending the data to database as the intent of "start riding"
- Once user has reached its destination station, he/she put back the bike, sending the data again to the database as the intent of "finished riding"

For each activity, there are data transactions between user and database. And how do you think each user's phone communicate with the server for storing and receiving the data? Using API ofcourse! 

We will later create a simplified version of the API service which handles data transactions and analysis. 


**Goals**: Make an API service to connect 3rd party user with data using HTTP request

**End Product**: A Flask API which capable of doing: 
- Input new data to database
- Read specific data from database
- Get specific insight from data analysis process (ie: best performing stations)

**Scoring Metrics**: 

1. 1 point - Created Flask App

-  create app.py file to make flask app
-  create Flask app to execute all of the endpoint you have made

2. 2 points - Created functionality to read or get specific data from the database

- create query to read data from database
- create function to execute read specific information into table from database

3. 4 points - Created functionality to input new data into each table for the databases

- create query to insert new data into stations and trips table
- create function to execute input data into stations and trips table

4. 3 points - Created static endpoints which return analytical result (must be different from point 2,3)

- create query to make analytical resultfrom the data
- create static endpoint to analyze the data from database, for example average trip durations
    
5. 3 points - Created dynamic endpoints which return analytical result (must be different from point 2,3,4)

- create query to make analytical resultfrom the data
- create dinamic endpoint to analyze the data from database, for example average trip durations for each bike_id

6. 3 points - Created POST endpoint which receive input data, then utilize it to get analytical result (must be different from point 2,3,4,5)

- create input data for refering into query for post endpoint
- make query and aggregation function to implement the input

**Tools**: 
- **Python** with **Jupyter Notebook**, installed with **required libraries**
- **Visual Studio Code (VSCode)**: Recommended for writing application scripts
- **TablePlus**: Recommended for easy database access and exploration
- Postman: Optional for easy API testing


# About the Data

The data that we will be using in this project is **[Austin Bike Share]()** dataset which contains information on bike trip start location, stop location, duration, type of bike share user in the city of Austin, Texas. Bike station location data is also provided. 

All the information is stored in a database called **austin_bikeshare.db**. However, we also provides the non existing data in csv files. These data then will be imported into the database using the API

Lists of files:
- **austin_bikeshare.db**: The database, contains `trips` and `stations` table
- **data/austin_bikeshare_stations.csv**: contains all the stations information which is not yet available in the database table
- **data/austin_bikeshare_trips_2021.csv**: contains all 2021 data which is not yet available in the database table

In [2]:
# Reading the csv data
trips = pd.read_csv('data/austin_bikeshare_trips_2021.csv')
stations = pd.read_csv('data/austin_bikeshare_stations.csv')

## Taking a look for trips data
`trips` table in database, or `austin_bikeshare_trips.csv` in original files. It roughly consisted of 1.3 million rows

In [42]:
trips.head(2)

trip_id subscriber_type bikeid               start_time  start_station_id  \
0  23455589        Local365    174  2021-01-26 17:47:42 UTC            4059.0   
1  23459960        Local365  19265  2021-01-28 08:03:52 UTC            4054.0   

                start_station_name  end_station_id end_station_name  \
0  Nash Hernandez/East @ RBJ South          3660.0  East 6th/Medina   
1                  Rosewood/Chicon          4055.0     11th/Salina    

   duration_minutes  
0                 7  
1                16

**Data Descriptions**:
- `bikeid`: integer id of bike
- `checkout_time`: HH:MM:SS, see start time for date stamp
- `duration_minutes`: int minutes of trip duration
- `endstationid`: integer id of end station
- `endstationname`: string of end station name
- `month`: month, integer
- `startstationid`: integer id of start station
- `startstationname`: string of start station name
- `start_time`: YYYY-MM-DD HH:MM:SS
- `subscriber_type`: membership typ e.g. walk up, annual, other bike share, etc
- `trip_id`: unique trip id int
- `year`: year of trip, int

## Taking a look for stations data
`stations` table in database, or `austin_bikeshare_stations.csv` in original files 

In [43]:
stations.tail(2)

station_id                  name  status                 address  \
96        3795  Dean Keeton & Whitis  active  300 W. Dean Keeton St.   
97        3797     21st & University  active    2007 University Ave.   

   alternate_name  city_asset_number         property_type  number_of_docks  \
96            NaN            32671.0  undetermined_parking             19.0   
97            NaN            32674.0  undetermined_parking             19.0   

   power_type  footprint_length  footprint_width                   notes  \
96      solar              55.0              5.0                     NaN   
97      solar              55.0              5.0  ROW might belong to UT   

    council_district         modified_date  
96                 9  2021-01-04T12:00:00Z  
97                 9  2021-01-04T12:00:00Z

In [44]:
stations.head()

station_id                             name  status             address  \
0        3464                       Pease Park  closed   1155 Kingsbury St   
1        2500                  Republic Square  closed    425 W 4th Street   
2        2536                 Waller & 6th St.  closed      602 Waller St.   
3        2538  Bullock Museum @ Congress & MLK  closed  1881 Congress Ave.   
4        2541  State Capitol @ 14th & Colorado  closed     206 W. 14th St.   

  alternate_name  city_asset_number property_type  number_of_docks power_type  \
0            NaN                NaN           NaN              NaN        NaN   
1            NaN                NaN           NaN              NaN        NaN   
2            NaN                NaN           NaN              NaN        NaN   
3            NaN                NaN           NaN              NaN        NaN   
4            NaN                NaN           NaN              NaN        NaN   

   footprint_length  footprint_width notes  council_district  \
0               NaN              NaN   NaN                 9   
1               NaN              NaN   NaN                 9   
2               NaN              NaN   NaN                 3   
3               NaN              NaN   NaN                 1   
4               NaN              NaN   NaN                 1   

          modified_date  
0  2021-01-04T12:00:00Z  
1  2021-01-04T12:00:00Z  
2  2021-01-04T12:00:00Z  
3  2021-01-04T12:00:00Z  
4  2021-01-04T12:00:00Z

**stations table (or austin_bikeshare_trips.csv)**:
- `station_id`: integer id of station
- `name`: string of station name
- `status`: string of station status (active, closed, moved, ACL-only)
- `address`: string of station address
- `alternate_name`: string of station alternative name
- `city_asset_number`: integer of station's asset number
- `property_type`: string of station's property type
- `number_of_docks`: integer of number of available bike docks
- `power_type`: string of station's power source type
- `footprint_length`: float of station' blueprint length (size of the station). Probably in meters
- `footprint_width`: float of station' blueprint width (size of the station). Probably in meters
- `notes`: string of additional notes
- `council_district`: integer of stations's council district
- `modified_date`: date of last modified information regarding the station

In [45]:
stations.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 98 entries, 0 to 97
Data columns (total 14 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   station_id         98 non-null     int64  
 1   name               98 non-null     object 
 2   status             98 non-null     object 
 3   address            98 non-null     object 
 4   alternate_name     2 non-null      object 
 5   city_asset_number  77 non-null     float64
 6   property_type      78 non-null     object 
 7   number_of_docks    77 non-null     float64
 8   power_type         78 non-null     object 
 9   footprint_length   77 non-null     float64
 10  footprint_width    77 non-null     float64
 11  notes              26 non-null     object 
 12  council_district   98 non-null     int64  
 13  modified_date      98 non-null     object 
dtypes: float64(4), int64(2), object(8)
memory usage: 10.8+ KB


# Database

The first important task is to make sure we can securely make connections to the database. In this scenario, we will connect to sqlite database, `austin_bikeshare.db` via python. In this part, we will re-visit on how to work with databases, started with making a connection, get some data, and insert data into it. 

You can directly connect and view the database using TablePlus, or run the following code to create the connection

In [3]:
# Define a function to create connection for reusability purpose
def make_connection():
    connection = sqlite3.connect('austin_bikeshare.db')
    return connection

# Make a connection
conn = make_connection()

## POST: Insert data into database

Generally, POST method will utilize the data sent by user for specific purporse, for example: 

- Insert new data into the database. 
- Operate the data into some function

We will learn how to insert data into a specific table in our database. Please refer to the following code to create and run the query for the given task

In [47]:
#data = 
stations.iloc[21]
#data.info()
#tuple(data.fillna('').values)

station_id                           3687
name                       Boardwalk West
status                             active
address              300 E. Riverside Dr.
alternate_name                        NaN
city_asset_number                 16683.0
property_type                    parkland
number_of_docks                       9.0
power_type                          solar
footprint_length                     30.0
footprint_width                       5.0
notes                                 NaN
council_district                        9
modified_date        2021-01-04T12:00:00Z
Name: 21, dtype: object

In [11]:
data1 = stations.iloc[21]
data1 = data1.astype(object)
data1.info()

<class 'pandas.core.series.Series'>
Index: 14 entries, station_id to modified_date
Series name: 21
Non-Null Count  Dtype 
--------------  ----- 
12 non-null     object
dtypes: object(1)
memory usage: 780.0+ bytes


In [12]:
data = tuple(int(x) if isinstance(x, (np.int64, np.int32)) else x for x in stations.iloc[21].fillna('').values)
data


(3687,
 'Boardwalk West',
 'active',
 '300 E. Riverside Dr.',
 '',
 16683.0,
 'parkland',
 9.0,
 'solar',
 30.0,
 5.0,
 '',
 9,
 '2021-01-04T12:00:00Z')

In [13]:
inset_query = "INSERT INTO stations VALUES (VALUE1,VALUE2,VALUE3,..VALUEN)"

In [48]:
# Get the data values #data = tuple(int(x) if isinstance(x, (np.int64, np.int32)) else x for x in stations.iloc[21].fillna('').values)
data = tuple(stations.iloc[20].fillna('').values)
# Make the query
query = f"""
INSERT INTO stations
VALUES {data}
"""

In [49]:
# See the actual query looks like
print(query)


INSERT INTO stations
VALUES (2502, 'Barton Springs & Riverside', 'closed', '400 Barton Springs Rd.', '', '', ' ', '', ' ', '', '', 'moved to Pedernales/2nd. Original city ID: 16729', 9, '2021-01-04T12:00:00Z')



In [50]:
# Execute the query 
conn.execute(query)

In [51]:
# Commit changes to database
conn.commit()

Once the code above succesful, it's recomended to wrap it into a function so that we can reuse it in the future. Complete the following codes to make the function:

In [52]:
def insert_into_stations(data, conn):
    query = f"""INSERT INTO stations values {data}"""
    try:
        conn.execute(query)
    except Exception as e:
        return print(f"Error: {e}")
    conn.commit()
    return 'OK'

In [55]:
# Example use of the function 
conn = make_connection()
data = tuple(stations.iloc[10].fillna('').values) # Randomly select a data
result = insert_into_stations(data, conn)

In [56]:
result

'OK'

In [40]:
#conn.close()

**TASK: Create a Function to insert data for `trips` table**

In [126]:
# Your code here
def insert_into_trips(data, conn):
    query = f""" 
            INSERT INTO trips
            VALUES {data}
            """
    try:
        conn.execute(query)
    except Exception as e:
        return f"{e}"
    conn.commit()
    return 'OK;'


In [130]:
conn = make_connection()
data = tuple(trips.iloc[8].fillna('').values) # Randomly select a data
result = insert_into_trips(data, conn)
result

'OK;'

In [129]:
conn.commit()

In [61]:
trips.iloc[7]

trip_id                                23458858
subscriber_type                        Local365
bikeid                                    19688
start_time              2021-01-27 17:15:40 UTC
start_station_id                         4062.0
start_station_name    Lakeshore/Pleasant Valley
end_station_id                           4062.0
end_station_name      Lakeshore/Pleasant Valley
duration_minutes                             12
Name: 7, dtype: object

In [60]:
query="""SELECT * FROM trips"""
pd.read_sql_query(query,conn).tail(5)

id          subscriber_type bikeid               start_time  \
1324080  20400249  U.T. Student Membership   171G  2019-07-31 16:51:17 UTC   
1324081  22837019                 Local365  19660  2020-09-17 14:21:51 UTC   
1324082  23184844                 Local365  19427  2020-11-13 17:02:07 UTC   
1324083  23184851                 Local365  16456  2020-11-13 17:02:51 UTC   
1324084  23458858                 Local365  19688  2021-01-27 17:15:40 UTC   

        start_station_id         start_station_name end_station_id  \
1324080             3838                26th/Nueces           4061   
1324081             3838                26th/Nueces           4061   
1324082             3838                26th/Nueces           4061   
1324083             3838                26th/Nueces           4061   
1324084             4062  Lakeshore/Pleasant Valley           4062   

                  end_station_name  duration_minutes  
1324080    Lakeshore/Austin Hostel                58  
1324081    Lakeshore/Austin Hostel                68  
1324082    Lakeshore/Austin Hostel                40  
1324083    Lakeshore/Austin Hostel                40  
1324084  Lakeshore/Pleasant Valley                12

## GET: Read specific data

Generally, GET method will ask for specific the data in the database, alongside with additional information we might send. For example: 
- Get number of unique user
- Get full trips information for specific user id
- Get average trips duration and length for specific user id

In this example, we will implement the most basic GET method, that is to get Station information in the table based on specific Station ID

In [66]:
# Get Specific Station ID  Query
station_id = 2502
query_station_id = f"""
SELECT * FROM stations
WHERE station_id = {station_id}
"""

# Get all station ID Query
query_station_all = "SELECT * FROM stations"

In [67]:
print(query_station_id)


SELECT * FROM stations
WHERE station_id = 2502



In [68]:
# Run the query and get the result
result = pd.read_sql_query(query_station_id, conn)

In [69]:
result

station_id                        name  status                 address  \
0        2502  Barton Springs & Riverside  closed  400 Barton Springs Rd.   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             

  footprint_length footprint_width  \
0                                    

                                              notes  council_district  \
0  moved to Pedernales/2nd. Original city ID: 16729                 9   

          modified_date  
0  2021-01-04T12:00:00Z

Just like the previous section, create a function to read specific station

In [71]:
def get_station_id(station_id, conn):
    query = f"""SELECT * FROM stations WHERE station_id = {station_id}"""
    result = pd.read_sql_query(query, conn)
    return result 

def get_all_stations(conn):
    query = f"""SELECT * FROM stations"""
    result = pd.read_sql_query(query, conn)
    return result

In [73]:
test = get_all_stations(conn)
test

station_id                        name  status                 address  \
0        2502  Barton Springs & Riverside  closed  400 Barton Springs Rd.   
1        1001     OFFICE/Main/Shop/Repair  active             1000 Brazos   
2        2712     Toomey Rd @ South Lamar  closed        1301 Toomey Road   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             
1                                                                             
2                                                                             

  footprint_length footprint_width  \
0                                    
1                                    
2                                    

                                              notes  council_district  \
0  moved to Pedernales/2nd. Original city ID: 16729                 9   
1                                                                   1   
2                                                                   5   

          modified_date  
0  2021-01-04T12:00:00Z  
1  2021-01-04T12:00:00Z  
2  2021-01-04T12:00:00Z

In [74]:
id = 2502
test = get_station_id(id,conn)
test

station_id                        name  status                 address  \
0        2502  Barton Springs & Riverside  closed  400 Barton Springs Rd.   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             

  footprint_length footprint_width  \
0                                    

                                              notes  council_district  \
0  moved to Pedernales/2nd. Original city ID: 16729                 9   

          modified_date  
0  2021-01-04T12:00:00Z

**TASK: Create a Function to read data from `trips` table**

In [75]:
# Your code here
def get_trip_id(trip_id, conn):
    query = f""" SELECT * FROM trips WHERE id = {trip_id}"""
    result = pd.read_sql_query(query,conn)
    return result

def get_all_trips(conn):
    query = f""" SELECT * FROM trips """
    result = pd.read_sql_query(query,conn)
    return result


In [76]:
result = get_all_trips(conn)
result.tail(5)

id          subscriber_type bikeid               start_time  \
1324080  20400249  U.T. Student Membership   171G  2019-07-31 16:51:17 UTC   
1324081  22837019                 Local365  19660  2020-09-17 14:21:51 UTC   
1324082  23184844                 Local365  19427  2020-11-13 17:02:07 UTC   
1324083  23184851                 Local365  16456  2020-11-13 17:02:51 UTC   
1324084  23458858                 Local365  19688  2021-01-27 17:15:40 UTC   

        start_station_id         start_station_name end_station_id  \
1324080             3838                26th/Nueces           4061   
1324081             3838                26th/Nueces           4061   
1324082             3838                26th/Nueces           4061   
1324083             3838                26th/Nueces           4061   
1324084             4062  Lakeshore/Pleasant Valley           4062   

                  end_station_name  duration_minutes  
1324080    Lakeshore/Austin Hostel                58  
1324081    Lakeshore/Austin Hostel                68  
1324082    Lakeshore/Austin Hostel                40  
1324083    Lakeshore/Austin Hostel                40  
1324084  Lakeshore/Pleasant Valley                12

In [77]:
id = 23458858
result = get_trip_id(id,conn)
result

id subscriber_type bikeid               start_time  start_station_id  \
0  23458858        Local365  19688  2021-01-27 17:15:40 UTC              4062   

          start_station_name  end_station_id           end_station_name  \
0  Lakeshore/Pleasant Valley            4062  Lakeshore/Pleasant Valley   

   duration_minutes  
0                12

# Flask App

Flask is a micro-framework for python. Generally we can build any application out of it. To start with, let's make our first empy flask app. 
Creata a new file `app.py`, then copy-paste the following codes into it and save it. 

*Notes: it's recomended to use vscode as editor since it support vast linting supports, including python which we find really helpful in coding*

```python
from flask import Flask, request
app = Flask(__name__) 

if __name__ == '__main__':
    app.run(debug=True, port=5000)
```

To run the app, you can open your terminal, go to the specific folder and run `python app.py` using your designated virtual environment

## Routes and Endpoints

### Implement endpoints

If you succesfully run the previous app and access the localhost:5000 , you might get an 404 not found error. This is because we **have not** define yet what will happen if people accessing our root path of the app (localhost:5000/)

Add the following example of route or endpoint into your `app.py` just before the `if __name__ === '__main__':` line, and reload the page to see if it works

```python 
@app.route('/')
def home():
    return 'Hello World'
```

Above endpoints will runs the `home` function anytime user access the `/` page.

Since we are going to handle all the requests through this app, the very next step is to implement our functionalites. Let's start with implementing the functionality to read all station data

we will add the `get_all_stations()` functions into our app, create a `@app.route('/stations/')` endpoint and call the function in it. The code should looks like:

```python 
@app.route('/stations/')
def route_all_stations():
    conn = make_connection()
    stations = get_all_stations(conn)
    return stations.to_json()
    
def get_all_stations(conn):
    query = f"""SELECT * FROM stations"""
    result = pd.read_sql_query(query, conn)
    return result
```

However, adding just above codes is not enough. If you see, there is a dependency inside the function, which is `make_connection()` function. Other than that, we will be using all the required libraries. 

Hence, we can complete the code by : 
- import the required libraries at the top of the `app.py` file
- write the `make_connection()` function before any routes declarations

Once it's completed, you should see no errors in the vscode screen, and your endpoint should work just fine and returns all the stations. It's now your task to impelement the `get_all_trips` into the app 

**TASK: Implement `get_all_trips()` method into the app** \
Place it under `@app.route('/trips/')` endpoint

In [ ]:
# your code
@app.route('/trips/')
def route_all_trips():
    conn = make_connection()
    trips = get_all_trips(conn)
    return trips.to_json()

def get_all_trips(conn):
    query = f"""SELECT * FROM trips LIMIT 5"""
    result = pd.read_sql_query(query,conn)
    print(result.head(5))
    return result

### Access Endpoints

To access our endpoints using python, simply use `requests` library followed by the request method (post, get, put, delete, etc) the passed in the url or data 

In [79]:
url = 'http://127.0.0.1:5000/stations/'
res = requests.get(url)

In [80]:
res

<Response [200]>

The response sent by the server was not only contains bare data. It was packed as HTTP response, meaning that we need to unpack the response first  in order to get the data. we can use `res.json()` to obtain it, then use pandas to transform it into dataframe for readibility or future analysis purposes. 

In [82]:
pd.DataFrame(res.json()).head()

station_id                        name  status                 address  \
0        2502  Barton Springs & Riverside  closed  400 Barton Springs Rd.   
1        1001     OFFICE/Main/Shop/Repair  active             1000 Brazos   
2        2712     Toomey Rd @ South Lamar  closed        1301 Toomey Road   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             
1                                                                             
2                                                                             

  footprint_length footprint_width  \
0                                    
1                                    
2                                    

                                              notes  council_district  \
0  moved to Pedernales/2nd. Original city ID: 16729                 9   
1                                                                   1   
2                                                                   5   

          modified_date  
0  2021-01-04T12:00:00Z  
1  2021-01-04T12:00:00Z  
2  2021-01-04T12:00:00Z

## Static and Dynamic Endpoints

On previous part we already made several endpoints which control how our server will react whenever users access it. 
If we take a look at the endpoints, it's all static : 
- `@app.route('/')`
- `@app.route('/home/')`
- `@app.route('/stations/')`
- `@app.route('/trips/')`


What if, instead of getting all the stations information, we only wanted to read a specific station information of station_id 3464 ? \
should we make an excact endpoint of that like `@app.route('stations/3464')`?. But what about the others? are we going to make a bunch of endpoints for each specific id like: 
- `@app.route('/stations/3464')`
- `@app.route('/stations/2500')`
- `@app.route('/stations/2541')`
- and so on...

Of course we shouldn't. One way to overcome the problem is by delcaring a **dynamic endpoints**. Basically, it's an endpoint which allows user to insert a variable values in it. The final looks of the dynamic endpoint version of above problem is: 
- `@app.route('stations/<station_id>')`

From above endpoint, the \<station_id\> is the variable, and we need to make sure that it influence how our following function acts. The whole dynamic endpoints for getting specific station by its id will looks like: 

```python 
@app.route('/stations/<station_id>')
def route_stations_id(station_id):
    conn = make_connection()
    station = get_station_id(station_id, conn)
    return station.to_json()
```


Before accesing the endpoint, make sure that `make_connection()` and `get_station_id()` functions are included inside `app.py` script so that it won't raise an error. Now for the final step, we can try to access the dynamic endpoints by changing the `station_id` in the following codes

In [85]:
station_id = 2502
url = f"http://127.0.0.1:5000/stations/{station_id}"

In [86]:
response = requests.get(url)
#response.txt
pd.DataFrame(response.json())

station_id                        name  status                 address  \
0        2502  Barton Springs & Riverside  closed  400 Barton Springs Rd.   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             

  footprint_length footprint_width  \
0                                    

                                              notes  council_district  \
0  moved to Pedernales/2nd. Original city ID: 16729                 9   

          modified_date  
0  2021-01-04T12:00:00Z

**TASK: Implement dynamic endpoints to read specific trip by its trip_id!** \
Place it under `@app.route('/trips/<trip_id>')` endpoint

In [87]:
url = f"http://127.0.0.1:5000/trips"
res = requests.get(url)
pd.DataFrame(res.json())

id                 subscriber_type bikeid  \
0        9900289692                         Walk Up    248   
1        9900285987  24-Hour Kiosk (Austin B-cycle)    446   
2        9900285989  24-Hour Kiosk (Austin B-cycle)    203   
3        9900285991  24-Hour Kiosk (Austin B-cycle)    101   
4        9900286140  24-Hour Kiosk (Austin B-cycle)    242   
...             ...                             ...    ...   
1324080    20400249         U.T. Student Membership   171G   
1324081    22837019                        Local365  19660   
1324082    23184844                        Local365  19427   
1324083    23184851                        Local365  16456   
1324084    23458858                        Local365  19688   

                      start_time start_station_id  \
0        2015-10-02 21:12:01 UTC             1006   
1        2014-10-26 15:12:00 UTC             2712   
2        2014-10-26 15:12:00 UTC             2712   
3        2014-10-26 15:12:00 UTC             2712   
4        2014-10-26 18:12:00 UTC             2541   
...                          ...              ...   
1324080  2019-07-31 16:51:17 UTC             3838   
1324081  2020-09-17 14:21:51 UTC             3838   
1324082  2020-11-13 17:02:07 UTC             3838   
1324083  2020-11-13 17:02:51 UTC             3838   
1324084  2021-01-27 17:15:40 UTC             4062   

                      start_station_name end_station_id  \
0                       Zilker Park West           1008   
1                Toomey Rd @ South Lamar           2712   
2                Toomey Rd @ South Lamar           2712   
3                Toomey Rd @ South Lamar           2712   
4        State Capitol @ 14th & Colorado           2541   
...                                  ...            ...   
1324080                      26th/Nueces           4061   
1324081                      26th/Nueces           4061   
1324082                      26th/Nueces           4061   
1324083                      26th/Nueces           4061   
1324084        Lakeshore/Pleasant Valley           4062   

                        end_station_name  duration_minutes  
0                           Nueces @ 3rd                39  
1                Toomey Rd @ South Lamar                31  
2                Toomey Rd @ South Lamar                31  
3                Toomey Rd @ South Lamar                30  
4        State Capitol @ 14th & Colorado                19  
...                                  ...               ...  
1324080          Lakeshore/Austin Hostel                58  
1324081          Lakeshore/Austin Hostel                68  
1324082          Lakeshore/Austin Hostel                40  
1324083          Lakeshore/Austin Hostel                40  
1324084        Lakeshore/Pleasant Valley                12  

[1324085 rows x 9 columns]

In [99]:
trips_id = 23458858
url = f"http://127.0.0.1:5000/trips/{trips_id}"
res = requests.get(url)
pd.DataFrame(res.json())

id subscriber_type bikeid               start_time  start_station_id  \
0  23458858        Local365  19688  2021-01-27 17:15:40 UTC              4062   

          start_station_name  end_station_id           end_station_name  \
0  Lakeshore/Pleasant Valley            4062  Lakeshore/Pleasant Valley   

   duration_minutes  
0                12

In [100]:
id = 9900286140
url=f"http://127.0.0.1:5000/trips/{id}"
rest = requests.get(url)
pd.DataFrame(rest.json())

id                 subscriber_type bikeid               start_time  \
0  9900286140  24-Hour Kiosk (Austin B-cycle)    242  2014-10-26 18:12:00 UTC   

   start_station_id               start_station_name  end_station_id  \
0              2541  State Capitol @ 14th & Colorado            2541   

                  end_station_name  duration_minutes  
0  State Capitol @ 14th & Colorado                19

## Handling JSON data as input

Sometimes, in order to make something happens in our API, we need the user to send us the data. In this case, we need to handle how we can get the data (which mostly sent as json format) and utilize it inside our endpoint functions. 

In order to achieve that, we will be using flask's `request` classes.


```python
@app.route('/json', methods=['POST']) 
def json_example():
    
    req = request.get_json(force=True) # Parse the incoming json data as Dictionary
    
    name = req['name']
    age = req['age']
    address = req['address']
    
    return (f'''Hello {name}, your age is {age}, and your address in {address}
            ''')
```

In [111]:
#@app.route('/json', methods=['POST']) 
def json_example():
    
    req = request.get_json(force=True) # Parse the incoming json data as Dictionary
    
    name = req['name']
    age = req['age']
    address = req['address']
    Job = req['Job']
    Work = req['Work']
    
    return (f'''Hello {name}, your age is {age}, and your address in {address}, saat ini kerja di {Work}, sebagai {Job}
            ''')

In [102]:
data = {
    "name" : "Andi", 
    "age" : 24,
    "address" : "my adress"
}

url = "http://127.0.0.1:5000/json"

In [112]:
data = {
    "name" : "Hadiat", 
    "age" : 30,
    "address" : "my adress",
    "Job" : "Ass. Section Chief",
    "Work" : "PT Asahimas Flat Glass tbk"
}

url = "http://127.0.0.1:5000/json"

In [113]:
res = requests.post(url, json=data)

In [114]:
res

<Response [200]>

In [115]:
res.text

'Hello Hadiat, your age is 30, and your address in my adress\n            '

In [ ]:
pd.DataFrame(res.json())

Now that we already know how to handle json input, we can try to implement and endpoint in which we can insert new data into `stations` table. 

```python

@app.route('/stations/add', methods=['POST']) 
def route_add_station():
    # parse and transform incoming data into a tuple as we need 
    data = pd.Series(eval(request.get_json(force=True)))
    data = tuple(data.fillna('').values)
    
    conn = make_connection()
    result = insert_into_stations(data, conn)
    return result


```

In [137]:
class NpEncoder(json.JSONEncoder):
    def default(self, obj):
        if isinstance(obj, np.integer):
            return int(obj)
        if isinstance(obj, np.floating):
            return float(obj)
        if isinstance(obj, np.ndarray):
            return obj.tolist()
        return super(NpEncoder, self).default(obj)

In [153]:
data = stations.iloc[26].fillna('').to_dict()
data_json = json.dumps(data, cls=NpEncoder)
data_json

'{"station_id": 2707, "name": "Rainey St @ Cummings", "status": "active", "address": "1 Rainey St", "alternate_name": "", "city_asset_number": 16597.0, "property_type": "parkland", "number_of_docks": 17.0, "power_type": "solar", "footprint_length": 50.0, "footprint_width": 5.0, "notes": "parkland at ROW/easement", "council_district": 9, "modified_date": "2021-01-04T12:00:00Z"}'

In [154]:
url = "http://127.0.0.1:5000/stations/add"
res = requests.post(url, json=data_json)

In [155]:
res

<Response [200]>

In [156]:
res.text

'OK'

In [152]:
#conn.close()
#conn.commit()

In [22]:
#conn = make_connection()

In [157]:
# Sintaks for iteratively insert stations (from stations_csv) into stations table
for idx, data in tqdm(stations.iterrows()):
    data = data.fillna('').to_dict()
    data_json = json.dumps(data, cls=NpEncoder)
    
    url = "http://127.0.0.1:5000/stations/add"
    res = requests.post(url, json=data_json)


98it [02:35,  1.59s/it]


In [158]:
res

<Response [200]>

In [161]:
url = "http://127.0.0.1:5000/stations/"
rest1 = requests.get(url)
pd.DataFrame(rest1.json()).info()

<class 'pandas.core.frame.DataFrame'>
Index: 90 entries, 0 to 89
Data columns (total 14 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   station_id         90 non-null     int64 
 1   name               90 non-null     object
 2   status             90 non-null     object
 3   address            90 non-null     object
 4   alternate_name     90 non-null     object
 5   city_asset_number  90 non-null     object
 6   property_type      90 non-null     object
 7   number_of_docks    90 non-null     object
 8   power_type         90 non-null     object
 9   footprint_length   90 non-null     object
 10  footprint_width    90 non-null     object
 11  notes              90 non-null     object
 12  council_district   90 non-null     int64 
 13  modified_date      90 non-null     object
dtypes: int64(2), object(12)
memory usage: 10.5+ KB


**TASK: Using the API, insert all the trips data (in csv) into the database by running the following codes**\
It might run differently on each devices, so you might get some rest while waiting for it to complete

In [162]:
for idx, data in tqdm(trips.iterrows()):
    data = data.fillna('').to_dict()
    data_json = json.dumps(data, cls=NpEncoder)
    
    url = "http://127.0.0.1:5000/trips/add"
    res = requests.post(url, json=data_json)

0it [00:00, ?it/s]

17982it [50:07,  5.98it/s]


In [163]:
res

<Response [200]>

In [165]:
res.text

'OK'

In [176]:
conn = make_connection()

In [177]:
query = """SELECT *
        FROM trips
        WHERE start_time like '2021%'
          """
data_2021 = pd.read_sql_query(query,conn,parse_dates='start_time')
data_2021.head()

id subscriber_type bikeid                start_time  \
0  23458858        Local365  19688 2021-01-27 17:15:40+00:00   
1  23442084        Local365   1471 2021-01-22 16:59:16+00:00   
2  23455589        Local365    174 2021-01-26 17:47:42+00:00   
3  23459960        Local365  19265 2021-01-28 08:03:52+00:00   
4  23436548        Local365  18331 2021-01-21 07:09:48+00:00   

   start_station_id               start_station_name  end_station_id  \
0              4062        Lakeshore/Pleasant Valley            4062   
1              4050                     5th/Campbell            3685   
2              4059  Nash Hernandez/East @ RBJ South            3660   
3              4054                  Rosewood/Chicon            4055   
4              4055                     11th/Salina             4055   

            end_station_name  duration_minutes  
0  Lakeshore/Pleasant Valley                12  
1              9th/Henderson                15  
2            East 6th/Medina                 7  
3               11th/Salina                 16  
4               11th/Salina                 25

In [178]:
data_2021.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17976 entries, 0 to 17975
Data columns (total 9 columns):
 #   Column              Non-Null Count  Dtype              
---  ------              --------------  -----              
 0   id                  17976 non-null  int64              
 1   subscriber_type     17976 non-null  object             
 2   bikeid              17976 non-null  object             
 3   start_time          17976 non-null  datetime64[ns, UTC]
 4   start_station_id    17976 non-null  int64              
 5   start_station_name  17976 non-null  object             
 6   end_station_id      17976 non-null  int64              
 7   end_station_name    17976 non-null  object             
 8   duration_minutes    17976 non-null  int64              
dtypes: datetime64[ns, UTC](1), int64(4), object(4)
memory usage: 1.2+ MB


In [174]:
query = """SELECT *
        FROM trips
          """
data_trips = pd.read_sql_query(query,conn,parse_dates='start_time')

In [175]:
data_trips.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1342060 entries, 0 to 1342059
Data columns (total 9 columns):
 #   Column              Non-Null Count    Dtype              
---  ------              --------------    -----              
 0   id                  1342060 non-null  int64              
 1   subscriber_type     1342060 non-null  object             
 2   bikeid              1342060 non-null  object             
 3   start_time          1342060 non-null  datetime64[ns, UTC]
 4   start_station_id    1342060 non-null  object             
 5   start_station_name  1342060 non-null  object             
 6   end_station_id      1342060 non-null  object             
 7   end_station_name    1342060 non-null  object             
 8   duration_minutes    1342060 non-null  int64              
dtypes: datetime64[ns, UTC](1), int64(2), object(6)
memory usage: 92.2+ MB


In [184]:
data_trips['year']= data_trips['start_time'].dt.year

In [185]:
data_trips['year'].unique()

array([2015, 2014, 2017, 2013, 2016, 2018, 2019, 2020, 2021])

In [15]:
### ANALISA TIPE DATA QUERY
# 
query = """ SELECT * FROM stations
        WHERE status IS 'closed'        
"""
pd.read_sql_query(query,conn).head()

station_id                        name  status                 address  \
0        2502  Barton Springs & Riverside  closed  400 Barton Springs Rd.   
1        2712     Toomey Rd @ South Lamar  closed        1301 Toomey Road   
2        3464                  Pease Park  closed       1155 Kingsbury St   
3        2500             Republic Square  closed        425 W 4th Street   
4        2536            Waller & 6th St.  closed          602 Waller St.   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             
1                                                                             
2                                                                             
3                                                                             
4                                                                             

  footprint_length footprint_width  \
0                                    
1                                    
2                                    
3                                    
4                                    

                                              notes  council_district  \
0  moved to Pedernales/2nd. Original city ID: 16729                 9   
1                                                                   5   
2                                                                   9   
3                                                                   9   
4                                                                   3   

          modified_date  
0  2021-01-04T12:00:00Z  
1  2021-01-04T12:00:00Z  
2  2021-01-04T12:00:00Z  
3  2021-01-04T12:00:00Z  
4  2021-01-04T12:00:00Z

In [20]:
#status = input('Masukan status: ')
status = "closed"
query = f""" 
        SELECT * FROM stations WHERE status IS '{status}'
        """
print(query)

 
        SELECT * FROM stations WHERE status IS 'closed'
        


In [21]:
pd.read_sql_query(query,conn).tail()

station_id                name  status               address  \
15        1006    Zilker Park West  closed     Barton Springs Rd   
16        1007        Lavaca & 6th  closed        601 Lavaca St.   
17        1008        Nueces @ 3rd  closed            311 Nueces   
18        2540    17th & Guadalupe  closed       411 W. 17th St.   
19        3635  13th & San Antonio  closed  1285 San Antonio St.   

   alternate_name city_asset_number property_type number_of_docks power_type  \
15                                                                             
16                                                                             
17                                                                             
18                            16739  paid_parking              12      solar   
19                            32522  paid_parking              13      solar   

   footprint_length footprint_width notes  council_district  \
15                                                        8   
16                                                        9   
17                                                        9   
18             40.0             5.0                       9   
19             40.0             5.0                       9   

           modified_date  
15  2021-01-04T12:00:00Z  
16  2021-01-04T12:00:00Z  
17  2021-01-04T12:00:00Z  
18  2021-03-12T01:02:00Z  
19  2021-03-12T12:49:00Z

In [22]:
def get_status_station(status_station,conn):
    query = f""" 
        SELECT * FROM stations WHERE status IS '{status_station}'
        """
    result = pd.read_sql_query(query,conn)
    return result
    

In [24]:
status = "closed"
res = get_status_station(status,conn)
res.tail()

station_id                name  status               address  \
15        1006    Zilker Park West  closed     Barton Springs Rd   
16        1007        Lavaca & 6th  closed        601 Lavaca St.   
17        1008        Nueces @ 3rd  closed            311 Nueces   
18        2540    17th & Guadalupe  closed       411 W. 17th St.   
19        3635  13th & San Antonio  closed  1285 San Antonio St.   

   alternate_name city_asset_number property_type number_of_docks power_type  \
15                                                                             
16                                                                             
17                                                                             
18                            16739  paid_parking              12      solar   
19                            32522  paid_parking              13      solar   

   footprint_length footprint_width notes  council_district  \
15                                                        8   
16                                                        9   
17                                                        9   
18             40.0             5.0                       9   
19             40.0             5.0                       9   

           modified_date  
15  2021-01-04T12:00:00Z  
16  2021-01-04T12:00:00Z  
17  2021-01-04T12:00:00Z  
18  2021-03-12T01:02:00Z  
19  2021-03-12T12:49:00Z

In [38]:
status= input('Masukan data: ')
url=f"http://127.0.0.1:5000/{status}"
rest = requests.get(url)
rest

<Response [200]>

In [39]:
pd.DataFrame(rest.json()).head()

station_id                        name  status                 address  \
0        2502  Barton Springs & Riverside  closed  400 Barton Springs Rd.   
1        2712     Toomey Rd @ South Lamar  closed        1301 Toomey Road   
2        3464                  Pease Park  closed       1155 Kingsbury St   
3        2500             Republic Square  closed        425 W 4th Street   
4        2536            Waller & 6th St.  closed          602 Waller St.   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             
1                                                                             
2                                                                             
3                                                                             
4                                                                             

  footprint_length footprint_width  \
0                                    
1                                    
2                                    
3                                    
4                                    

                                              notes  council_district  \
0  moved to Pedernales/2nd. Original city ID: 16729                 9   
1                                                                   5   
2                                                                   9   
3                                                                   9   
4                                                                   3   

          modified_date  
0  2021-01-04T12:00:00Z  
1  2021-01-04T12:00:00Z  
2  2021-01-04T12:00:00Z  
3  2021-01-04T12:00:00Z  
4  2021-01-04T12:00:00Z

In [42]:
#ditemukan pola dimana status yang kedua dianggap dinamis oleh stations akan dibuat lebih deskriptif
status= input('Masukan data: ')
url=f"http://127.0.0.1:5000/stations/status/{status}"
rest = requests.get(url)
rest

<Response [200]>

In [43]:
pd.DataFrame(rest.json()).head()

station_id                     name  status                  address  \
0        1001  OFFICE/Main/Shop/Repair  active              1000 Brazos   
1        3684  Congress & Cesar Chavez  active    124 W Cesar Chavez St   
2        2572      Barton Springs Pool  active  2200 William Barton Dr.   
3        2707     Rainey St @ Cummings  active              1 Rainey St   
4        3294             Lavaca & 6th  active        619 Guadalupe St.   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             
1                            32594      parkland              11      solar   
2                            16758      parkland              13      solar   
3                            16597      parkland              17      solar   
4                            32515      sidewalk              12      solar   

  footprint_length footprint_width                     notes  \
0                                                              
1             35.0             5.0  parkland at ROW/easement   
2             40.0             5.0                             
3             50.0             5.0  parkland at ROW/easement   
4             25.0             7.5   double sided, remeasure   

   council_district         modified_date  
0                 1  2021-01-04T12:00:00Z  
1                 9  2021-01-04T12:00:00Z  
2                 8  2021-01-04T12:00:00Z  
3                 9  2021-01-04T12:00:00Z  
4                 9  2021-01-04T12:00:00Z

# Make your own analytic endpoints

Based on what we've learned before, create your own endpoints which returns analytical result such as contigency tables, aggregation tables, or even just a values.

*ps: if the return is dataframe/series, don't forget to change it into json with `.to_json()` method*


- [x] 1 point - Created Flask App
- [x] 2 points - Created functionality to read or get specific data from the database
- [x] 4 points - Created functionality to input new data into each table for the databases
- [ ] 3 points - Created static endpoints which return analytical result (must be different from point 2,3)
- [ ] 3 points - Created dynamic endpoints which return analytical result (must be different from point 2,3,4)
- [ ] 3 points - Created POST endpoint which receive input data, then utilize it to get analytical result (must be different from point 2,3,4,5)


## Create Static Endpoint(s)

You can use the following cell to try-out your function before implementing it as an endpoint.

After created the endpoint, make sure to implement it to `app.py` file.

**Your Code Here**

```python
# example of analytical static endpoint
@app.route('/trips/average_duration') 
    # your code
```

In [49]:
#average duration berada dicolumn duraration trips
query = """ 
        SELECT * FROM trips
        LIMIT 5
        """
pd.read_sql_query(query,conn)

id                 subscriber_type bikeid               start_time  \
0  9900289692                         Walk Up    248  2015-10-02 21:12:01 UTC   
1  9900285987  24-Hour Kiosk (Austin B-cycle)    446  2014-10-26 15:12:00 UTC   
2  9900285989  24-Hour Kiosk (Austin B-cycle)    203  2014-10-26 15:12:00 UTC   
3  9900285991  24-Hour Kiosk (Austin B-cycle)    101  2014-10-26 15:12:00 UTC   
4  9900286140  24-Hour Kiosk (Austin B-cycle)    242  2014-10-26 18:12:00 UTC   

   start_station_id               start_station_name  end_station_id  \
0              1006                 Zilker Park West            1008   
1              2712          Toomey Rd @ South Lamar            2712   
2              2712          Toomey Rd @ South Lamar            2712   
3              2712          Toomey Rd @ South Lamar            2712   
4              2541  State Capitol @ 14th & Colorado            2541   

                  end_station_name  duration_minutes  
0                     Nueces @ 3rd                39  
1          Toomey Rd @ South Lamar                31  
2          Toomey Rd @ South Lamar                31  
3          Toomey Rd @ South Lamar                30  
4  State Capitol @ 14th & Colorado                19

In [51]:
#buat rata-rata mean pada column duration_minutes
query = """ 
        SELECT bikeid, AVG(duration_minutes) as 'AVERAGE_DURATION'
        FROM trips
        GROUP BY bikeid
        ORDER BY AVERAGE_DURATION DESC
"""

pd.read_sql_query(query,conn)

bikeid  AVERAGE_DURATION
0    Block05       3385.000000
1    Block02        671.800000
2      21495        367.392857
3      21709        236.923077
4      19456        225.265957
..       ...               ...
948    21800         14.571429
949    21767         14.062500
950    21473          9.000000
951    14244          4.000000
952  Block03          2.000000

[953 rows x 2 columns]

In [52]:
###masukan ke fungis 
def average_duration(conn):
    query = """ 
        SELECT bikeid, AVG(duration_minutes) as 'AVERAGE_DURATION'
        FROM trips
        GROUP BY bikeid
        ORDER BY AVERAGE_DURATION DESC
        """
    result = pd.read_sql_query(query,conn)
    return result


In [53]:
#### call fungsi
res = average_duration(conn)
res.head(5)

bikeid  AVERAGE_DURATION
0  Block05       3385.000000
1  Block02        671.800000
2    21495        367.392857
3    21709        236.923077
4    19456        225.265957

```
@app.route('/average_duration/')
def route_average_duration():
    conn = make_connection()
    average = average_duration(conn)
    return average.to_json()

In [54]:
url = f'http://127.0.0.1:5000/average_duration/'
res = requests.get(url)
pd.DataFrame(res.json()).head(5)

bikeid  AVERAGE_DURATION
0  Block05       3385.000000
1  Block02        671.800000
2    21495        367.392857
3    21709        236.923077
4    19456        225.265957

*Ambil data berdasarkan tahun*
dimana query yang dipakai adalah:
```'''```python 
query = """ 
        SELECT * FROM trips
        WHERE start_time Like '/year/'

"""
@app.route('/trips/<year>')
def route_trips_year(year):
    conn = make_connection()
    year = get_trip_year(year, conn)
    return year.to_json() 


'''

In [12]:
#Fungsi mendapatkan tahun
def get_trip_year(tahun, conn):
    query = f""" SELECT * FROM trips WHERE start_time LIKE '{tahun}%' """
    result = pd.read_sql_query(query,conn)
    return result

In [13]:
#tahun = input('Masukan tahun yang ingin di check:')
tahun = 2016
res = get_trip_year(tahun,conn)
res


id subscriber_type bikeid               start_time  \
0         10987762        Local365    141  2016-07-17 21:25:00 UTC   
1         10846121         Walk Up    461  2016-07-08 08:35:53 UTC   
2         10748754         Walk Up    571  2016-07-02 10:30:31 UTC   
3       9900018958        Local365     60  2016-01-23 17:12:08 UTC   
4         13012172         Walk Up    549  2016-11-29 13:05:53 UTC   
...            ...             ...    ...                      ...   
184675    11067992        Local365    577  2016-07-22 17:24:43 UTC   
184676    11067993        Local365    920  2016-07-22 17:24:45 UTC   
184677    10928319        Local365    178  2016-07-13 19:16:15 UTC   
184678    13022711        Local365     55  2016-11-30 08:09:57 UTC   
184679    13023370        Local365    101  2016-11-30 09:17:45 UTC   

       start_station_id start_station_name end_station_id  \
0                  1007       Lavaca & 6th           3464   
1                  1007       Lavaca & 6th           1007   
2                  1007       Lavaca & 6th           1007   
3                  1008       Nueces @ 3rd           1008   
4                  3464         Pease Park           3464   
...                 ...                ...            ...   
184675             2552         3rd & West           3513   
184676             2552         3rd & West           3513   
184677             2552         3rd & West           3513   
184678             2552         3rd & West           3619   
184679             2552         3rd & West           3619   

                                         end_station_name  duration_minutes  
0                                              Pease Park                 7  
1                                            Lavaca & 6th               110  
2                                            Lavaca & 6th                33  
3                                            Nueces @ 3rd                 4  
4                                              Pease Park                46  
...                                                   ...               ...  
184675  South Congress & Barton Springs at the Austin ...               399  
184676  South Congress & Barton Springs at the Austin ...                10  
184677  South Congress & Barton Springs at the Austin ...                12  
184678                                     6th & Congress                 7  
184679                                     6th & Congress                 5  

[184680 rows x 9 columns]

**TEST YOUR ENDPOINT**

After implement it to `app.py` file, **test and implement** your **static endpoint** with the following cells.

In [ ]:
# test static endpoint
url = 'http://127.0.0.1:5000/<your_endpoint>/'
res = requests.get(url)
res

In [ ]:
# show the result as dataframe
pd.DataFrame(res.json())

In [4]:
#trial tahun 
tahun = 2021
url=f"http://127.0.0.1:5000/trips/tahun/{tahun}"
print(url)


http://127.0.0.1:5000/trips/tahun/2021


In [5]:
rest = requests.get(url)
rest.text

'{"id":{"0":23458858,"1":23442084,"2":23455589,"3":23459960,"4":23436548,"5":23382542,"6":23374882,"7":23431885,"8":23369810,"9":23421503,"10":23420169,"11":23472134,"12":23469658,"13":23374367,"14":23386724,"15":23408347,"16":23404059,"17":23386787,"18":23409721,"19":23409718,"20":23376382,"21":23448759,"22":23424431,"23":23468653,"24":23377690,"25":23370199,"26":23370869,"27":23371118,"28":23371141,"29":23371138,"30":23373196,"31":23371600,"32":23372300,"33":23374971,"34":23375131,"35":23375071,"36":23375217,"37":23375220,"38":23378921,"39":23376666,"40":23442283,"41":23454565,"42":23377729,"43":23399538,"44":23460073,"45":23380939,"46":23379817,"47":23459138,"48":23387119,"49":23395380,"50":23398638,"51":23404314,"52":23418167,"53":23418128,"54":23422024,"55":23419579,"56":23442484,"57":23443741,"58":23443333,"59":23436454,"60":23436794,"61":23439891,"62":23462697,"63":23466431,"64":23451688,"65":23453446,"66":23470461,"67":23419522,"68":23420767,"69":23473013,"70":23419531,"71":233

In [6]:
pd.DataFrame(rest.json())

id          subscriber_type bikeid               start_time  \
0      23458858                 Local365  19688  2021-01-27 17:15:40 UTC   
1      23442084                 Local365   1471  2021-01-22 16:59:16 UTC   
2      23455589                 Local365    174  2021-01-26 17:47:42 UTC   
3      23459960                 Local365  19265  2021-01-28 08:03:52 UTC   
4      23436548                 Local365  18331  2021-01-21 07:09:48 UTC   
...         ...                      ...    ...                      ...   
17971  23515345                 Local365  19476  2021-02-13 14:17:15 UTC   
17972  23553979                 Local365  19418  2021-02-26 18:12:13 UTC   
17973  23499655  U.T. Student Membership  21553  2021-02-07 17:15:29 UTC   
17974  23538444  U.T. Student Membership   2147  2021-02-22 20:52:06 UTC   
17975  23536417                 Local365  16410  2021-02-22 13:41:36 UTC   

       start_station_id               start_station_name  end_station_id  \
0                  4062        Lakeshore/Pleasant Valley            4062   
1                  4050                     5th/Campbell            3685   
2                  4059  Nash Hernandez/East @ RBJ South            3660   
3                  4054                  Rosewood/Chicon            4055   
4                  4055                     11th/Salina             4055   
...                 ...                              ...             ...   
17971              3838                      26th/Nueces            3841   
17972              3838                      26th/Nueces            3841   
17973              3838                      26th/Nueces            3841   
17974              3838                      26th/Nueces            3841   
17975              3838                      26th/Nueces            3841   

                end_station_name  duration_minutes  
0      Lakeshore/Pleasant Valley                12  
1                  9th/Henderson                15  
2                East 6th/Medina                 7  
3                   11th/Salina                 16  
4                   11th/Salina                 25  
...                          ...               ...  
17971            23rd/Rio Grande                62  
17972            23rd/Rio Grande                 4  
17973            23rd/Rio Grande                 3  
17974            23rd/Rio Grande               704  
17975            23rd/Rio Grande                63  

[17976 rows x 9 columns]

In [23]:
#Analisa hubungan antara Stations dan Trips
query =""" 
        SELECT trips.*, stations.status, stations.power_type
        FROM trips
        LEFT JOIN stations
            ON trips.start_station_id = stations.station_id
"""
data_status = pd.read_sql_query(query,conn)

In [25]:
data_status.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1342060 entries, 0 to 1342059
Data columns (total 11 columns):
 #   Column              Non-Null Count    Dtype 
---  ------              --------------    ----- 
 0   id                  1342060 non-null  int64 
 1   subscriber_type     1342060 non-null  object
 2   bikeid              1342060 non-null  object
 3   start_time          1342060 non-null  object
 4   start_station_id    1342060 non-null  object
 5   start_station_name  1342060 non-null  object
 6   end_station_id      1342060 non-null  object
 7   end_station_name    1342060 non-null  object
 8   duration_minutes    1342060 non-null  int64 
 9   status              1195835 non-null  object
 10  power_type          1195835 non-null  object
dtypes: int64(2), object(9)
memory usage: 112.6+ MB


In [26]:
data_status['status']=data_status['status'].astype('category')
data_status['status'].unique()

['closed', 'active', NaN]
Categories (2, object): ['active', 'closed']

In [37]:
data_status.groupby('status')['status'].size()

C:\Users\user\AppData\Local\Temp\ipykernel_16968\2678720068.py:1: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  data_status.groupby('status')['status'].size()


status
active    1097560
closed      98275
Name: status, dtype: int64

In [31]:
data_status['status'].isna().sum()

146225

In [38]:
data_status['start_time'] = pd.to_datetime(data_status['start_time'])

In [39]:
data_status['year'] =data_status['start_time'].dt.year

In [40]:
status_pertahun = data_status.groupby(['year','status']).size()
status_pertahun

C:\Users\user\AppData\Local\Temp\ipykernel_16968\768420153.py:1: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  status_pertahun = data_status.groupby(['year','status']).size()


year  status
2013  active      1130
      closed       212
2014  active    103952
      closed     23303
2015  active    126470
      closed     32292
2016  active    139641
      closed     22629
2017  active    158413
      closed     11474
2018  active    360004
      closed      6504
2019  active    100438
      closed      1213
2020  active     90970
      closed       648
2021  active     16542
      closed         0
dtype: int64

Problem di atas kita buat ke app

In [69]:
query = """ 
        SELECT SUBSTR(REPLACE(start_time, ' UTC', ''), 1, 4) AS year, status, COUNT(stations.status) as 'TotalStatus'
        FROM trips
        LEFT JOIN stations
            ON trips.start_station_id = stations.station_id
        GROUP BY year, status
        ORDER BY year, status
        """
pd.read_sql_query(query,conn).head(5)

year  status  TotalStatus
0  2013    None            0
1  2013  active         1130
2  2013  closed          212
3  2014    None            0
4  2014  active       103952

### MARI KITA BUAT STATIC UNTUK MENGHITUN JUMLAH status station yang aktif dan closed setiap tahun, termasuk yang tidak ada status, let's go

In [ ]:
#buat fungsi
def total_status_year(conn):
    query = """ 
        SELECT SUBSTR(REPLACE(start_time, ' UTC', ''), 1, 4) AS year, status, COUNT(stations.status) as 'TotalStatus'
        FROM trips
        LEFT JOIN stations
            ON trips.start_station_id = stations.station_id
        GROUP BY year, status
        ORDER BY year, status """
    result = pd.read_sql_query(query,conn)
    return result

In [72]:
#panggil fungsi
res = total_status_year(conn)
res

year  status  TotalStatus
0   2013    None            0
1   2013  active         1130
2   2013  closed          212
3   2014    None            0
4   2014  active       103952
5   2014  closed        23303
6   2015    None            0
7   2015  active       126470
8   2015  closed        32292
9   2016    None            0
10  2016  active       139641
11  2016  closed        22629
12  2017    None            0
13  2017  active       158413
14  2017  closed        11474
15  2018    None            0
16  2018  active       360004
17  2018  closed         6504
18  2019    None            0
19  2019  active       100438
20  2019  closed         1213
21  2020    None            0
22  2020  active        90970
23  2020  closed          648
24  2021    None            0
25  2021  active        16542

```
@app.route('/total_status_year/')
def route_total_status_year():
    conn = make_connection()
    total = total_status_year(conn)
    return total.to_json()

In [74]:
url = 'http://127.0.0.1:5000/total_status_year/'
res = requests.get(url)
pd.DataFrame(res.json())

year  status  TotalStatus
0   2013    None            0
1   2013  active         1130
2   2013  closed          212
3   2014    None            0
4   2014  active       103952
5   2014  closed        23303
6   2015    None            0
7   2015  active       126470
8   2015  closed        32292
9   2016    None            0
10  2016  active       139641
11  2016  closed        22629
12  2017    None            0
13  2017  active       158413
14  2017  closed        11474
15  2018    None            0
16  2018  active       360004
17  2018  closed         6504
18  2019    None            0
19  2019  active       100438
20  2019  closed         1213
21  2020    None            0
22  2020  active        90970
23  2020  closed          648
24  2021    None            0
25  2021  active        16542

In [21]:
#Hubungkan antara tahun dan status stations dengan banyaknya 
query =""" 
        SELECT trips.*, stations.status, stations.power_type
        FROM trips
        LEFT JOIN stations
            ON trips.start_station_id = stations.station_id
        WHERE stations.status IS 'active'
"""
pd.read_sql_query(query,conn).value_counts(ascending=True)

id          subscriber_type          bikeid  start_time               start_station_id  start_station_name                                      end_station_id  end_station_name                            duration_minutes  status  power_type 
8269933     Local365                 195     2016-01-01 00:27:51 UTC  2563              Davis at Rainey Street                                  2563            Davis at Rainey Street                      2                 active  solar          1
20885253    Local365                 1555    2019-09-24 12:55:55 UTC  2566              Electric Drive/Sandra Muraida Way @ Pfluger Ped Bridge  2567            Barton Springs/Bouldin @ Palmer Auditorium  5                 active  solar          1
20885348    Local365                 1596    2019-09-24 13:05:12 UTC  2552              3rd/West                                                2501            5th/Bowie                                   2                 active  solar          1
20885356    Local

In [ ]:
query =""" 
        SELECT trips.*, stations.status, stations.power_type
        FROM trips
        LEFT JOIN stations
            ON trips.start_station_id = stations.station_id
        WHERE stations.status IS 'closed'
"""
pd.read_sql_query(query,conn).shape

## Create Static Endpoints 
#dengan menggabungkan dua table stations dan trips
#Join menggunakna start_station_id

In [46]:
def get_all_table(conn):
    query = """ 
        SELECT trips.*, stations.status, stations.power_type,stations.modified_date
        FROM trips
        LEFT JOIN stations
            ON trips.start_station_id = stations.station_id
        """
    result = pd.read_sql_query(query,conn)
    return result

In [47]:
join_table = get_all_table(conn)
join_table.head(5)

id                 subscriber_type bikeid               start_time  \
0  9900289692                         Walk Up    248  2015-10-02 21:12:01 UTC   
1  9900285987  24-Hour Kiosk (Austin B-cycle)    446  2014-10-26 15:12:00 UTC   
2  9900285989  24-Hour Kiosk (Austin B-cycle)    203  2014-10-26 15:12:00 UTC   
3  9900285991  24-Hour Kiosk (Austin B-cycle)    101  2014-10-26 15:12:00 UTC   
4  9900286140  24-Hour Kiosk (Austin B-cycle)    242  2014-10-26 18:12:00 UTC   

  start_station_id               start_station_name end_station_id  \
0             1006                 Zilker Park West           1008   
1             2712          Toomey Rd @ South Lamar           2712   
2             2712          Toomey Rd @ South Lamar           2712   
3             2712          Toomey Rd @ South Lamar           2712   
4             2541  State Capitol @ 14th & Colorado           2541   

                  end_station_name  duration_minutes  status power_type  \
0                     Nueces @ 3rd                39  closed              
1          Toomey Rd @ South Lamar                31  closed              
2          Toomey Rd @ South Lamar                31  closed              
3          Toomey Rd @ South Lamar                30  closed              
4  State Capitol @ 14th & Colorado                19  closed              

          modified_date  
0  2021-01-04T12:00:00Z  
1  2021-01-04T12:00:00Z  
2  2021-01-04T12:00:00Z  
3  2021-01-04T12:00:00Z  
4  2021-01-04T12:00:00Z

##OK maka kita buat untuk flash
```
@app.route('/join/') 
def route_all_table():
    conn = make_connection()
    join = get_all_table( conn)
    return join.to_json() 


In [48]:
#mari kita test
url = f'http://127.0.0.1:5000/join'
res = requests.get(url)
pd.DataFrame(res.json())

id                 subscriber_type bikeid  \
0        9900289692                         Walk Up    248   
1        9900285987  24-Hour Kiosk (Austin B-cycle)    446   
2        9900285989  24-Hour Kiosk (Austin B-cycle)    203   
3        9900285991  24-Hour Kiosk (Austin B-cycle)    101   
4        9900286140  24-Hour Kiosk (Austin B-cycle)    242   
...             ...                             ...    ...   
1342055    23515345                        Local365  19476   
1342056    23553979                        Local365  19418   
1342057    23499655         U.T. Student Membership  21553   
1342058    23538444         U.T. Student Membership   2147   
1342059    23536417                        Local365  16410   

                      start_time start_station_id  \
0        2015-10-02 21:12:01 UTC             1006   
1        2014-10-26 15:12:00 UTC             2712   
2        2014-10-26 15:12:00 UTC             2712   
3        2014-10-26 15:12:00 UTC             2712   
4        2014-10-26 18:12:00 UTC             2541   
...                          ...              ...   
1342055  2021-02-13 14:17:15 UTC             3838   
1342056  2021-02-26 18:12:13 UTC             3838   
1342057  2021-02-07 17:15:29 UTC             3838   
1342058  2021-02-22 20:52:06 UTC             3838   
1342059  2021-02-22 13:41:36 UTC             3838   

                      start_station_name end_station_id  \
0                       Zilker Park West           1008   
1                Toomey Rd @ South Lamar           2712   
2                Toomey Rd @ South Lamar           2712   
3                Toomey Rd @ South Lamar           2712   
4        State Capitol @ 14th & Colorado           2541   
...                                  ...            ...   
1342055                      26th/Nueces           3841   
1342056                      26th/Nueces           3841   
1342057                      26th/Nueces           3841   
1342058                      26th/Nueces           3841   
1342059                      26th/Nueces           3841   

                        end_station_name  duration_minutes  status power_type  \
0                           Nueces @ 3rd                39  closed              
1                Toomey Rd @ South Lamar                31  closed              
2                Toomey Rd @ South Lamar                31  closed              
3                Toomey Rd @ South Lamar                30  closed              
4        State Capitol @ 14th & Colorado                19  closed              
...                                  ...               ...     ...        ...   
1342055                  23rd/Rio Grande                62  active      solar   
1342056                  23rd/Rio Grande                 4  active      solar   
1342057                  23rd/Rio Grande                 3  active      solar   
1342058                  23rd/Rio Grande               704  active      solar   
1342059                  23rd/Rio Grande                63  active      solar   

                modified_date  
0        2021-01-04T12:00:00Z  
1        2021-01-04T12:00:00Z  
2        2021-01-04T12:00:00Z  
3        2021-01-04T12:00:00Z  
4        2021-01-04T12:00:00Z  
...                       ...  
1342055  2021-01-04T12:00:00Z  
1342056  2021-01-04T12:00:00Z  
1342057  2021-01-04T12:00:00Z  
1342058  2021-01-04T12:00:00Z  
1342059  2021-01-04T12:00:00Z  

[1342060 rows x 12 columns]

## Create Dynamic Endpoints 

You can use the following cell to try-out your function before implementing it as an endpoint.

After created the endpoint, make sure to implement it to `app.py` file.

**Your Code Here**

```python
# example of analytical dynamic endpoint
@app.route('/trips/average_duration/<bike_id>')
    # code here
```

In [58]:
#kita buat fungis terlebih dahulu
def average_duration_bike_id(bike_id,conn):
    query = f""" 
        SELECT bikeid, AVG(duration_minutes) as 'AVERAGE_DURATION'
        FROM trips
        WHERE bikeid IS '{bike_id}'
        """
    result = pd.read_sql_query(query,conn)
    return result

In [60]:
#test
bike_id = "Block05"
res = average_duration_bike_id(bike_id,conn)
res

bikeid  AVERAGE_DURATION
0  Block05            3385.0

```
@app.route('/trips/average_duration/<bike_id>')
def route_average_duration_bikeid(bike_id):
    conn = make_connection()
    average = average_duration_bike_id(bike_id,conn)
    return average.to_json()

In [ ]:
bike_id = "Block05"

In [63]:
bike_id = "202"

In [64]:
#jika OK mari kita buat fungsi route untuk app

url = f'http://127.0.0.1:5000/trips/average_duration/{bike_id}'
res = requests.get(url)
pd.DataFrame(res.json())

bikeid  AVERAGE_DURATION
0    202         26.090391

**TEST YOUR ENDPOINT**

After implement it to `app.py` file, **test and implement** your **dynamic endpoint** with the following cells.

Disini kami akan menghitung tahun dari trips dan berapa yang close maupun active
dengan metode statci sebelumnya 

In [88]:
def total_status_peryear(tahun,conn):
    query = f""" 
        SELECT SUBSTR(REPLACE(start_time, ' UTC', ''), 1, 4) AS year, status, COUNT(stations.status) as 'TotalStatus'
        FROM trips
        LEFT JOIN stations
            ON trips.start_station_id = stations.station_id
        GROUP BY year,status
            HAVING year IS '{tahun}'
         """
    result = pd.read_sql_query(query,conn)
    return result

In [89]:
tahun = 2015
test = total_status_peryear(tahun,conn)
test

year  status  TotalStatus
0  2015    None            0
1  2015  active       126470
2  2015  closed        32292

In [107]:
#bagaimana jika kita ingin lihat tahun dan status stationnya
#saya inign mengisi tahun, kemudian kondisi, jika kondisi kosong menghitung semuanya
def total_status_station_peryear(tahun,status_station,conn):
    query = f""" 
        SELECT SUBSTR(REPLACE(start_time, ' UTC', ''), 1, 4) AS year, status, COUNT(stations.status) as 'TotalStatus'
        FROM trips
        LEFT JOIN stations
            ON trips.start_station_id = stations.station_id
        GROUP BY year,status
            HAVING (year IS '{tahun}') AND  (status = '{status_station}' OR '{status_station}' = '' OR '{status_station}' IS NULL)
         """
    result = pd.read_sql_query(query,conn)
    return result

In [109]:
tahun = 2015
status_station = ""

test2 = total_status_station_peryear(tahun,status_station,conn)
test2

year  status  TotalStatus
0  2015    None            0
1  2015  active       126470
2  2015  closed        32292

#jika kodisi ok maka coba untuk app
```
@app.route ('/total_status_year/<tahun>/<status_station>')
def route_total_status_station_peryear(tahun,status_station):
    conn = make_connection()
    total1 = total_status_station_peryear(tahun,status_station,conn)
    return total1.to_json()


In [113]:
# test dynamic endpoint
tahun = 2015
status = "closed"
url = f'http://127.0.0.1:5000/total_status_year/{tahun}/{status}'
res = requests.get(url)
res

<Response [200]>

In [114]:
# show the result as dataframe
pd.DataFrame(res.json())

year  status  TotalStatus
0  2015  closed        32292

In [125]:
# test dynamic endpoint
tahun = 2015
status = "active"
url = f'http://127.0.0.1:5000/total_status_year/{tahun}/{status}'
res = requests.get(url)
res

<Response [200]>

In [126]:
pd.DataFrame(res.json())

year  status  TotalStatus
0  2015  active       126470

In [127]:
tahun = 2015
status = ""
url = f'http://127.0.0.1:5000/total_status_year/{tahun}/{status}'
print(url)
res = requests.get(url)
res

http://127.0.0.1:5000/total_status_year/2015/


<Response [200]>

In [128]:
pd.DataFrame(res.json())

year  status  TotalStatus
0  2015    None            0
1  2015  active       126470
2  2015  closed        32292

## Create POST Endpoints

You can use the following cell to try-out your function before implementing it as an endpoint.

If you still find it quite difficult, here's an example case you might wanted to try on:
- input : a dictionary contained a datetime period
    - { "period" : "2015-08" }
- output:
    - Aggregation table of bike rent activities for each station in that specific period
- example code: 

```python 
input_data = request.get_json() # Get the input as dictionary
specified_date = input_data['period'] # Select specific items (period) from the dictionary (the value will be "2015-08")

# Subset the data with query 
conn = make_connection()
query = f"SELECT * FROM stations WHERE start_time LIKE ({specified_date}%)"
selected_data = pd.read_sql_query(query, conn)

# Make the aggregate
result = selected_data.groupby('start_station_id').agg({
    'bikeid' : 'count', 
    'duration_minutes' : 'mean'
})

# Return the result
return result.to_json()

```

After created the endpoint, make sure to implement it to app.py file.

In [130]:
# Your Code Here
input = {"period" : "2015-08"}

In [144]:
#input_data = request.get_json()
input_data ={"period" : "2015-08"}
specified_date = input_data['period']
print(specified_date)

2015-08


In [147]:
query = """ SELECT * FROM stations """
pd.read_sql_query(query,conn).head(2)

station_id                        name  status                 address  \
0        2502  Barton Springs & Riverside  closed  400 Barton Springs Rd.   
1        1001     OFFICE/Main/Shop/Repair  active             1000 Brazos   

  alternate_name city_asset_number property_type number_of_docks power_type  \
0                                                                             
1                                                                             

  footprint_length footprint_width  \
0                                    
1                                    

                                              notes  council_district  \
0  moved to Pedernales/2nd. Original city ID: 16729                 9   
1                                                                   1   

          modified_date  
0  2021-01-04T12:00:00Z  
1  2021-01-04T12:00:00Z

In [150]:
conn = make_connection()
query = f"""SELECT * FROM trips WHERE start_time LIKE '{specified_date}%'"""
selected_data  = pd.read_sql_query(query,conn)
selected_data

id subscriber_type bikeid               start_time  \
0      9900230495        Local365    877  2015-08-13 14:12:00 UTC   
1      9900225071         Walk Up    575  2015-08-01 20:12:00 UTC   
2      9900225072         Walk Up    219  2015-08-01 20:12:00 UTC   
3      9900234583         Walk Up    344  2015-08-22 13:12:00 UTC   
4      9900224518         Walk Up    276  2015-08-01 08:12:00 UTC   
...           ...             ...    ...                      ...   
14518  9900227423        Local365    334  2015-08-06 18:12:00 UTC   
14519  9900229559        Local365    507  2015-08-10 19:12:00 UTC   
14520  9900233004        Local365    805  2015-08-18 18:12:00 UTC   
14521  9900236428        Local365    579  2015-08-26 18:12:00 UTC   
14522  9900238895        Local365    412  2015-08-31 19:12:00 UTC   

      start_station_id start_station_name end_station_id  \
0                 1007       Lavaca & 6th           1008   
1                 2576  Rainey @ River St           2576   
2                 2576  Rainey @ River St           2576   
3                 1008       Nueces @ 3rd           1008   
4                 2576  Rainey @ River St           2576   
...                ...                ...            ...   
14518             2552         3rd & West           2822   
14519             2552         3rd & West           2822   
14520             2552         3rd & West           2822   
14521             2552         3rd & West           2822   
14522             2552         3rd & West           2822   

                  end_station_name  duration_minutes  
0                     Nueces @ 3rd                 2  
1                Rainey @ River St                26  
2                Rainey @ River St                26  
3                     Nueces @ 3rd                59  
4                Rainey @ River St                46  
...                            ...               ...  
14518  East 6th at Robert Martinez                18  
14519  East 6th at Robert Martinez                17  
14520  East 6th at Robert Martinez                17  
14521  East 6th at Robert Martinez                17  
14522  East 6th at Robert Martinez                16  

[14523 rows x 9 columns]

In [152]:
# Make the aggregate
result = selected_data.groupby('start_station_id').agg({
    'bikeid' : 'count', 
    'duration_minutes' : 'mean'
})
result.to_json()

'{"bikeid":{"1007":91,"1008":311,"2494":791,"2495":590,"2496":250,"2497":440,"2498":427,"2499":635,"2501":694,"2502":422,"2503":292,"2504":213,"2536":106,"2537":290,"2538":229,"2539":394,"2540":173,"2541":84,"2542":147,"2544":122,"2545":46,"2547":119,"2548":199,"2549":297,"2550":296,"2552":430,"2561":128,"2562":193,"2563":260,"2564":308,"2565":249,"2566":503,"2567":306,"2568":112,"2569":210,"2570":321,"2571":150,"2572":314,"2575":643,"2576":226,"2707":655,"2711":501,"2712":241,"2822":189,"2823":58,"3291":50,"3292":71,"3293":40,"":707},"duration_minutes":{"1007":18.2307692308,"1008":13.2379421222,"2494":26.0341340076,"2495":15.4593220339,"2496":27.624,"2497":27.4136363636,"2498":22.018735363,"2499":18.0960629921,"2501":15.476945245,"2502":31.2819905213,"2503":29.0719178082,"2504":21.9530516432,"2536":32.1509433962,"2537":12.1206896552,"2538":25.3886462882,"2539":22.9035532995,"2540":26.9190751445,"2541":22.75,"2542":14.5238095238,"2544":14.8442622951,"2545":11.2608695652,"2547":52.48739

In [161]:
input = {'period':'2015-08'}
url = 'http://127.0.0.1:5000/sample'

In [162]:
res = requests.post(url, json=input)

In [163]:
res.text

'{"bikeid":{"1007":91,"1008":311,"2494":791,"2495":590,"2496":250,"2497":440,"2498":427,"2499":635,"2501":694,"2502":422,"2503":292,"2504":213,"2536":106,"2537":290,"2538":229,"2539":394,"2540":173,"2541":84,"2542":147,"2544":122,"2545":46,"2547":119,"2548":199,"2549":297,"2550":296,"2552":430,"2561":128,"2562":193,"2563":260,"2564":308,"2565":249,"2566":503,"2567":306,"2568":112,"2569":210,"2570":321,"2571":150,"2572":314,"2575":643,"2576":226,"2707":655,"2711":501,"2712":241,"2822":189,"2823":58,"3291":50,"3292":71,"3293":40,"":707},"duration_minutes":{"1007":18.2307692308,"1008":13.2379421222,"2494":26.0341340076,"2495":15.4593220339,"2496":27.624,"2497":27.4136363636,"2498":22.018735363,"2499":18.0960629921,"2501":15.476945245,"2502":31.2819905213,"2503":29.0719178082,"2504":21.9530516432,"2536":32.1509433962,"2537":12.1206896552,"2538":25.3886462882,"2539":22.9035532995,"2540":26.9190751445,"2541":22.75,"2542":14.5238095238,"2544":14.8442622951,"2545":11.2608695652,"2547":52.48739

In [164]:
pd.DataFrame(res.json())

bikeid  duration_minutes
1007      91         18.230769
1008     311         13.237942
2494     791         26.034134
2495     590         15.459322
2496     250         27.624000
2497     440         27.413636
2498     427         22.018735
2499     635         18.096063
2501     694         15.476945
2502     422         31.281991
2503     292         29.071918
2504     213         21.953052
2536     106         32.150943
2537     290         12.120690
2538     229         25.388646
2539     394         22.903553
2540     173         26.919075
2541      84         22.750000
2542     147         14.523810
2544     122         14.844262
2545      46         11.260870
2547     119         52.487395
2548     199         35.452261
2549     297         26.067340
2550     296         15.442568
2552     430          9.586047
2561     128         35.359375
2562     193         30.943005
2563     260         19.803846
2564     308         12.155844
2565     249         17.542169
2566     503         19.552684
2567     306         23.581699
2568     112         16.517857
2569     210         16.538095
2570     321         23.426791
2571     150         16.640000
2572     314         24.993631
2575     643         34.421462
2576     226         33.150442
2707     655         25.610687
2711     501         25.800399
2712     241         19.867220
2822     189         12.301587
2823      58         18.241379
3291      50         20.820000
3292      71         13.056338
3293      40         14.525000
         707         33.753890

**TEST YOUR ENDPOINT**

After implement it to `app.py` file, **test and implement** your **POST endpoint** with the following cells.

#Disini kami akan mencoba menginput tahun, dimana dengan tahun ini,
1. kami akan mendapatkan jumlah bike_id yang banyak
2. station yang disinggahi pertama terbanyak dalam bulan
3. End stattion terbanyak dalam bulan
4. rata-rata durasi perbulan

Let's go

In [166]:
#input data -> {'tahun':'2015'}
input_data = {'tahun' : '2015'}
spesifik_tahun = input_data['tahun']
spesifik_tahun

'2015'

In [171]:
### panggil data trips menggunakan filter di atas
conn = make_connection()
query = f""" 
        SELECT * FROM trips 
        WHERE start_time LIKE '{spesifik_tahun}%'
"""
data_tahun = pd.read_sql_query(query,conn,parse_dates=['start_time'])
data_tahun.head(5)

id subscriber_type bikeid                start_time  \
0  9900289692         Walk Up    248 2015-10-02 21:12:01+00:00   
1  9900290433        Local365    453 2015-10-02 21:12:42+00:00   
2  9900288594       Weekender    822 2015-10-01 19:12:12+00:00   
3  9900288695       Weekender    202 2015-10-01 08:12:20+00:00   
4  9900288777       Weekender    854 2015-10-01 16:12:17+00:00   

  start_station_id              start_station_name end_station_id  \
0             1006                Zilker Park West           1008   
1             1006                Zilker Park West           1008   
2             2568  East 11th St. at Victory Grill           2536   
3             2568  East 11th St. at Victory Grill           2536   
4             3291              11th & San Jacinto           1008   

   end_station_name  duration_minutes  
0      Nueces @ 3rd                39  
1      Nueces @ 3rd                15  
2  Waller & 6th St.                 3  
3  Waller & 6th St.                11  
4      Nueces @ 3rd                20

In [172]:
data_tahun['start_time'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 184521 entries, 0 to 184520
Series name: start_time
Non-Null Count   Dtype              
--------------   -----              
184521 non-null  datetime64[ns, UTC]
dtypes: datetime64[ns, UTC](1)
memory usage: 1.4 MB


In [173]:
data_tahun['bulan'] = data_tahun['start_time'].dt.month_name()
data_tahun.head(5)

id subscriber_type bikeid                start_time  \
0  9900289692         Walk Up    248 2015-10-02 21:12:01+00:00   
1  9900290433        Local365    453 2015-10-02 21:12:42+00:00   
2  9900288594       Weekender    822 2015-10-01 19:12:12+00:00   
3  9900288695       Weekender    202 2015-10-01 08:12:20+00:00   
4  9900288777       Weekender    854 2015-10-01 16:12:17+00:00   

  start_station_id              start_station_name end_station_id  \
0             1006                Zilker Park West           1008   
1             1006                Zilker Park West           1008   
2             2568  East 11th St. at Victory Grill           2536   
3             2568  East 11th St. at Victory Grill           2536   
4             3291              11th & San Jacinto           1008   

   end_station_name  duration_minutes    bulan  
0      Nueces @ 3rd                39  October  
1      Nueces @ 3rd                15  October  
2  Waller & 6th St.                 3  October  
3  Waller & 6th St.                11  October  
4      Nueces @ 3rd                20  October

In [199]:
result = data_tahun.groupby(['bulan','start_station_name']).agg({
    'duration_minutes' : 'mean',
    'start_station_name':'count',
})
result

duration_minutes  start_station_name
bulan     start_station_name                                            
April     17th & Guadalupe                 18.191176                 272
          2nd & Congress                   30.538781                 722
          3rd & West                       13.009740                 308
          4th & Congress                   22.311209                 678
          5th & Bowie                      15.392258                 775
...                                              ...                 ...
September Trinity & 6th Street             24.551971                 279
          UT West Mall @ Guadalupe         28.833333                 216
          Waller & 6th St.                 18.407583                 211
          West & 6th St.                   22.120370                 324
          Zilker Park                      30.668687                 495

[602 rows x 2 columns]

In [200]:
result.to_json()

'{"duration_minutes":{"(\'April\', \'17th & Guadalupe\')":18.1911764706,"(\'April\', \'2nd & Congress\')":30.5387811634,"(\'April\', \'3rd & West\')":13.0097402597,"(\'April\', \'4th & Congress\')":22.3112094395,"(\'April\', \'5th & Bowie\')":15.3922580645,"(\'April\', \'5th & San Marcos\')":21.6691176471,"(\'April\', \'8th & Congress\')":18.3076923077,"(\'April\', \'ACC - Rio Grande & 12th\')":22.4333333333,"(\'April\', \'ACC - West & 12th\')":33.6923076923,"(\'April\', \'Barton Springs & Riverside\')":44.1472868217,"(\'April\', \'Barton Springs @ Kinney Ave\')":27.5690909091,"(\'April\', \'Barton Springs Pool\')":34.0953488372,"(\'April\', \'Bullock Museum @ Congress & MLK\')":23.0840840841,"(\'April\', \'Capital Metro HQ - East 5th at Broadway\')":18.4347826087,"(\'April\', \'Capitol Station \\/ Congress & 11th\')":30.1515151515,"(\'April\', \'City Hall \\/ Lavaca & 2nd\')":36.6968838527,"(\'April\', \'Convention Center \\/ 3rd & Trinity\')":34.3657718121,"(\'April\', \'Convention C

In [212]:
result = data_tahun.pivot_table(index ='bulan',
                                columns='subscriber_type',
                                values='start_station_name',
                                aggfunc='count',
                                fill_value=0)
result['Total']=result.iloc[1].sum()
result

subscriber_type  7-Day  Annual  Annual (Boulder B-cycle)  \
bulan                                                      
April              345       0                         2   
August               0       0                         0   
December             0      17                         0   
February            56       0                         0   
January            161       0                         6   
July                 0       0                         0   
June                 0       0                         2   
March             2381       0                        32   
May                 62       0                         0   
November             0      59                         0   
October              0     158                         0   
September            0      40                         0   

subscriber_type  Annual (Cincy Red Bike)  Annual (Denver B-cycle)  \
bulan                                                               
April                                  1                       20   
August                                 0                       19   
December                               0                        0   
February                               0                       55   
January                                0                       18   
July                                   2                       13   
June                                   5                        0   
March                                 11                       42   
May                                    1                       24   
November                               0                        0   
October                                0                        0   
September                              0                        5   

subscriber_type  Annual (Kansas City B-cycle)  Annual (Madison B-cycle)  \
bulan                                                                     
April                                       0                        45   
August                                     15                         0   
December                                    0                         0   
February                                    6                        15   
January                                     0                         9   
July                                        9                         2   
June                                        0                         3   
March                                       1                        29   
May                                         0                         0   
November                                    0                         0   
October                                     0                         0   
September                                   0                         0   

subscriber_type  Annual (Nashville B-cycle)  Annual (San Antonio B-cycle)  \
bulan                                                                       
April                                     2                            30   
August                                    0                            13   
December                                  0                             0   
February                                  0                            13   
January                                   0                             3   
July                                     10                            13   
June                                      0                             6   
March                                     5                            47   
May                                       0                             8   
November                                  0                             0   
October                                   0                             0   
September                                 0                             1   

subscriber_type  Annual Member  ...  Founding Member  Local30 

@app.route('/data/', methodes=['POST'])
def get_data_bulan():
    input_data = request.get_json(force=True)
    spesifik_tahun = input_data['tahun']
    conn = make_connection()
    query = f""" 
            SELECT * FROM trips 
            WHERE start_time LIKE '{spesifik_tahun}%'
    """
    data_tahun = pd.read_sql_query(query,conn,parse_dates=['start_time'])
    data_tahun['bulan'] = data_tahun['start_time'].dt.month_name()      
    result = data_tahun.pivot_table(index ='bulan',
                                columns='subscriber_type',
                                values='start_station_name',
                                aggfunc='count',
                                fill_value=0)
result['Total']=result.iloc[1].sum()

    return result.to_json()

In [201]:
# test POST endpoint
data = {
    "tahun" : "2015"
}

# post endpoint
url = "http://127.0.0.1:5000/data"
res = requests.post(url, json = data)

# show code result
res

<Response [200]>

In [202]:
# show the result as dataframe
pd.DataFrame(res.json())

duration_minutes  \
('April', '17th & Guadalupe')                     18.191176   
('April', '2nd & Congress')                       30.538781   
('April', '3rd & West')                           13.009740   
('April', '4th & Congress')                       22.311209   
('April', '5th & Bowie')                          15.392258   
...                                                     ...   
('September', 'Trinity & 6th Street')             24.551971   
('September', 'UT West Mall @ Guadalupe')         28.833333   
('September', 'Waller & 6th St.')                 18.407583   
('September', 'West & 6th St.')                   22.120370   
('September', 'Zilker Park')                      30.668687   

                                           start_station_name  
('April', '17th & Guadalupe')                             272  
('April', '2nd & Congress')                               722  
('April', '3rd & West')                                   308  
('April', '4th & Congress')                               678  
('April', '5th & Bowie')                                  775  
...                                                       ...  
('September', 'Trinity & 6th Street')                     279  
('September', 'UT West Mall @ Guadalupe')                 216  
('September', 'Waller & 6th St.')                         211  
('September', 'West & 6th St.')                           324  
('September', 'Zilker Park')                              495  

[602 rows x 2 columns]

In [213]:
# test POST endpoint
data = {
    "tahun" : "2015"
}

# post endpoint
url = "http://127.0.0.1:5000/data"
res = requests.post(url, json = data)

# show code result
res

<Response [200]>

In [214]:
pd.DataFrame(res.json())

7-Day  Annual  Annual (Boulder B-cycle)  Annual (Cincy Red Bike)  \
April        345       0                         2                        1   
August         0       0                         0                        0   
December       0      17                         0                        0   
February      56       0                         0                        0   
January      161       0                         6                        0   
July           0       0                         0                        2   
June           0       0                         2                        5   
March       2381       0                        32                       11   
May           62       0                         0                        1   
November       0      59                         0                        0   
October        0     158                         0                        0   
September      0      40                         0                        0   

           Annual (Denver B-cycle)  Annual (Kansas City B-cycle)  \
April                           20                             0   
August                          19                            15   
December                         0                             0   
February                        55                             6   
January                         18                             0   
July                            13                             9   
June                             0                             0   
March                           42                             1   
May                             24                             0   
November                         0                             0   
October                          0                             0   
September                        5                             0   

           Annual (Madison B-cycle)  Annual (Nashville B-cycle)  \
April                            45                           2   
August                            0                           0   
December                          0                           0   
February                         15                           0   
January                           9                           0   
July                              2                          10   
June                              3                           0   
March                            29                           5   
May                               0                           0   
November                          0                           0   
October                           0                           0   
September                         0                           0   

           Annual (San Antonio B-cycle)  Annual Member  ...  Founding Member  \
April                                30              0  ...              142   
August                               13              0  ...              154   
December                              0             27  ...              190   
February                             13              0  ...              129   
January                               3              0  ...              116   
July                                 13              0  ...              178   
June                                  6              0  ...              162   
March                                47              0  ...              158   
May                                   8              0  ...              143   
November                              0             16  ...              141   
October                               0             23  ...              165   
September                             1             15  ...              182   

           Local30  Local365  Local365 Youth with helmet (age 13-17 riders)  \
April          932      3715                                              0   
August        1787      410

# Submission

After finishing your work of all the rubrics, the next step will be;

1. Prepare your `Bikeshare API.ipynb` file that has been edited with your code and wrangling data.
2. Prepare your `app.py` file for your Flask App. Make sure you have implemented all the endpoints to `app.py` (including your custom static, dynamic and post endpoints).
3. Submit your `Bikeshare API.ipynb` and `app.py` file in your github repository. The dataset is optional to post since it has big size to post. 

